# Charting BP's Stock Price With Plotly

The aim of this project is to develop our knowledge of Plotly's interactive charts library using BPs stockprice taken from the Pyfinance API.

In [1]:
import datetime as dt
import numpy as np
import pandas as pd
import pandas_datareader.data as web


In [19]:
# Standard plotly imports
import chart_studio.plotly as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from plotly.offline import iplot, init_notebook_mode
#Specifying a default theme
import plotly.io as pio
pio.templates.default = 'plotly'



# Using plotly + cufflinks in offline mode
import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

## Accessing Data From an API And Exporting To A CSV

In [3]:
#Accessed BP stock data from yahoo using the DataReader API

start = dt.datetime(2000,1,1)
end = dt.datetime(2020,5,7)

df = web.DataReader('BP', 'yahoo', start, end)
df.head()

High      Low     Open    Close     Volume  Adj Close
Date                                                                
2000-01-03  59.3125  58.5000  59.2500  58.8125  2039300.0  22.443216
2000-01-04  59.4375  58.2500  58.4375  58.5000  3825800.0  22.323963
2000-01-05  60.5000  57.7500  57.9375  60.5000  4055900.0  23.087173
2000-01-06  60.6250  59.3125  59.6875  60.6250  4034700.0  23.134871
2000-01-07  59.5000  58.5000  58.5000  59.5000  4027200.0  22.705570

In [4]:
df.tail()

High        Low   Open      Close      Volume  Adj Close
Date                                                                     
2020-05-01  23.209999  22.629999  22.92  22.830000  13474900.0  21.943537
2020-05-04  23.360001  22.530001  22.68  23.250000  14212700.0  22.347227
2020-05-05  24.730000  23.799999  24.42  23.870001  13556300.0  22.943155
2020-05-06  24.209999  23.520000  24.15  23.580000  11111900.0  22.664415
2020-05-07  24.590000  23.950001  24.35  24.059999  10125600.0  23.125776

In [5]:
#Move to csv

df.to_csv('bp.csv')

In [6]:
ls

Charting BP's Stock Price With Plotly.ipynb
bp.csv


## Reading Data From a CSV

In [7]:
df = pd.read_csv('bp.csv',parse_dates=True, index_col=0)
df.head()

High      Low     Open    Close     Volume  Adj Close
Date                                                                
2000-01-03  59.3125  58.5000  59.2500  58.8125  2039300.0  22.443216
2000-01-04  59.4375  58.2500  58.4375  58.5000  3825800.0  22.323963
2000-01-05  60.5000  57.7500  57.9375  60.5000  4055900.0  23.087173
2000-01-06  60.6250  59.3125  59.6875  60.6250  4034700.0  23.134871
2000-01-07  59.5000  58.5000  58.5000  59.5000  4027200.0  22.705570

In [8]:
df['Adj Close'].iplot()

## Data Manipulation And Visualisation

Creating a new column in our dataset with the 100 day moving average.

In [9]:
df['100ma'] = df['Adj Close'].rolling(window=100, min_periods=0).mean()
df.head()

High      Low     Open    Close     Volume  Adj Close  \
Date                                                                   
2000-01-03  59.3125  58.5000  59.2500  58.8125  2039300.0  22.443216   
2000-01-04  59.4375  58.2500  58.4375  58.5000  3825800.0  22.323963   
2000-01-05  60.5000  57.7500  57.9375  60.5000  4055900.0  23.087173   
2000-01-06  60.6250  59.3125  59.6875  60.6250  4034700.0  23.134871   
2000-01-07  59.5000  58.5000  58.5000  59.5000  4027200.0  22.705570   

                100ma  
Date                   
2000-01-03  22.443216  
2000-01-04  22.383590  
2000-01-05  22.618118  
2000-01-06  22.747306  
2000-01-07  22.738959

In [10]:
df[['100ma', 'Adj Close']].iplot(title = 'BP - 100ma and adj close')

In [11]:
df['Volume'].iplot(title= 'BP Daily Volume')

In [12]:
fig = make_subplots(
    rows=3, cols=1,
    specs=[[{"rowspan": 2}],
           [None],
           [{}]],
    shared_xaxes=True,
    vertical_spacing=0.04)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Adj Close'],
    name="Adj Close"),             
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['100ma'],
    name='100ma'),
    row=1, col=1)
          

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Volume'],
    name="Volume"),
    row=3, col=1)

fig.update_yaxes(title_text='Price ($)', row=1, col=1)
fig.update_yaxes(title_text='Volume', row=3, col=1)

fig.update_layout(showlegend=False, title_text='BP Share Price')
fig.show()


## Calculating A Simple Moving Average And Bollinger Bands

- Middle Band = 20 day moving average
- Upper Band = 20 day moving average + (20 Day standard deviation of price x 2) 
- Lower Band = 20 day moving average - (20 Day standard deviation of price x 2)

In [13]:
df['30ma'] = df['Adj Close'].rolling(window=20, min_periods=0).mean()
df['30std'] = df['Adj Close'].rolling(window=20, min_periods=0).std(ddof=0)
df['Upper Band'] = df['30ma'] + (df['30std'] * 2)
df['Lower Band'] = df['30ma'] - (df['30std'] * 2)
df.head()

High      Low     Open    Close     Volume  Adj Close  \
Date                                                                   
2000-01-03  59.3125  58.5000  59.2500  58.8125  2039300.0  22.443216   
2000-01-04  59.4375  58.2500  58.4375  58.5000  3825800.0  22.323963   
2000-01-05  60.5000  57.7500  57.9375  60.5000  4055900.0  23.087173   
2000-01-06  60.6250  59.3125  59.6875  60.6250  4034700.0  23.134871   
2000-01-07  59.5000  58.5000  58.5000  59.5000  4027200.0  22.705570   

                100ma       30ma     30std  Upper Band  Lower Band  
Date                                                                
2000-01-03  22.443216  22.443216  0.000000   22.443216   22.443216  
2000-01-04  22.383590  22.383590  0.059627   22.502843   22.264337  
2000-01-05  22.618118  22.618118  0.335227   23.288571   21.947664  
2000-01-06  22.747306  22.747306  0.366540   23.480386   22.014226  
2000-01-07  22.738959  22.738959  0.328268   23.395495   22.082423

In [14]:
fig = make_subplots(
    rows=3, cols=1,
    specs=[[{"rowspan": 2}],
           [None],
           [{}]],
    shared_xaxes=True,
    vertical_spacing=0.04)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Adj Close'],
    name="Adj Close",
    line_color = 'black'),             
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['30ma'],
    name='30ma'),
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Upper Band'],
    name='Upper Band',
    fill='tonexty',
    mode='lines'),
    row=1, col=1)
          
fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Lower Band'],
    name='Lower Band',
    fill='tonexty',
    mode='lines'),
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Volume'],
    name="Volume"),
    row=3, col=1)

fig.update_yaxes(title_text='Price (£)', row=1, col=1)
fig.update_yaxes(title_text='Volume', row=3, col=1)

fig.update_layout(showlegend=True, title_text='BP Share Price Data')
fig.show()


## Data Manipulation And Resampling

We current have daily data but let's resample it to 10 day data.

In [15]:
df_ohlc = df['Adj Close'].resample('10D').ohlc()
df_volume = df['Volume'].resample('10D').sum()

df_ohlc.head()

open       high        low      close
Date                                                  
2000-01-03  22.443216  23.134871  21.584597  21.584597
2000-01-13  21.894655  21.894655  20.869089  21.465351
2000-01-23  21.369949  21.369949  20.511337  20.797535
2000-02-02  20.582888  20.582888  17.506184  17.792387
2000-02-12  18.102448  18.794109  17.887791  17.887791

In [16]:
#Reset the index

df_ohlc.reset_index(inplace=True)
df_ohlc.head()


Date       open       high        low      close
0 2000-01-03  22.443216  23.134871  21.584597  21.584597
1 2000-01-13  21.894655  21.894655  20.869089  21.465351
2 2000-01-23  21.369949  21.369949  20.511337  20.797535
3 2000-02-02  20.582888  20.582888  17.506184  17.792387
4 2000-02-12  18.102448  18.794109  17.887791  17.887791

## A Simple Candlestick Chart

In [17]:
fig = go.Figure(data=[go.Candlestick(x=df_ohlc['Date'],
                                    open=df_ohlc['open'],
                                    high=df_ohlc['high'],
                                    low=df_ohlc['low'],
                                    close=df_ohlc['close'])])

fig.show()

## Developing Our Candlestick Chart

In [21]:
fig = make_subplots(
    rows=3, cols=1,
    specs=[[{"rowspan": 2}],
           [None],
           [{}]],
    shared_xaxes=True,
    vertical_spacing=0.04)

fig.add_trace(go.Candlestick(
    x=df_ohlc['Date'],
    open=df_ohlc['open'],
    high=df_ohlc['high'],
    low=df_ohlc['low'],
    close=df_ohlc['close'],
    name='Ohlc',
    line=dict(width=0.7)),             
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['30ma'],
    name='30ma',
    line=dict(width=0.7)),
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Upper Band'],
    name='Upper Band',
    line=dict(width=0.7)),
    row=1, col=1)
          
fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Lower Band'],
    name='Lower Band',
    line=dict(width=0.7)),
    row=1, col=1)

fig.add_trace(go.Scatter(
    x= df.index,
    y= df['Volume'],
    name="Volume"),
    row=3, col=1)

fig.update_yaxes(title_text='Price (£)', row=1, col=1)
fig.update_yaxes(title_text='Volume', row=3, col=1)

fig.update_layout(showlegend=True, 
                  title_text='BP Share Price',
                 xaxis_rangeslider_visible=False)
fig.show()
